In [287]:
import lightgbm as lgb
import numpy as np 
import matplotlib.pyplot as plt
import pandas as pd
import pathlib
from sklearn.model_selection import train_test_split
import seaborn as sns
from sklearn import metrics
from sklearn.datasets import load_breast_cancer
from sklearn.ensemble import GradientBoostingClassifier
from scipy.stats import randint as sp_randint
from scipy.stats import uniform as sp_uniform
from sklearn.impute import SimpleImputer
from sklearn.model_selection import RandomizedSearchCV, GridSearchCV
from sklearn.metrics import classification_report
from scipy.stats import uniform as sp_uniform
from sklearn.metrics import accuracy_score, f1_score, make_scorer, cohen_kappa_score
from lightgbm import LGBMClassifier
from sklearn.model_selection import learning_curve, ShuffleSplit

In [288]:
# Parse results data
results = pd.DataFrame()

for path in pathlib.Path('/Users/sam/Documents/projects/premier_league_predictions/data').rglob("*.csv"):
    data = pd.read_csv(path)
    results = pd.concat([results, data])
    
# Remove missing values    
results = results.drop(['Unnamed: 0','result_x','result_y','away_ppg_home_team','home_ppg_away_team'], axis=1)
#results = results.dropna(axis=0)
results = results[results.result.values != 'pp']
results = results[~pd.isnull(results.result.values)]


In [289]:
imp = SimpleImputer(missing_values=np.nan, strategy='mean')

In [291]:
results.shape

(2795, 13)

In [292]:
X = results.loc[:, results.columns != 'result'].values
imp.fit(X)

X = imp.transform(X)

y = results.iloc[:, -1].values

In [293]:
y_values = []

for value in y:
    if value == "home":
        y_values.append(0)
    elif value == "away":
        y_values.append(1)
    else:
        y_values.append(2)
        
y = y_values

In [294]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.33, random_state=42, shuffle=True)

In [249]:
parameters={"early_stopping_rounds":20, 
            "eval_metric" : 'multi_logloss', 
            "eval_set" : [(X_test,y_test)],
            'eval_names': ['valid'],
            'verbose': 100,
            'categorical_feature': 'auto'}

In [250]:
parameter_tuning ={
             'max_depth': sp_randint(1,5),
             'num_leaves': sp_randint(1, 5), 
             'learning_rate ': [1,0.1,0.01,0.001],
             'min_child_samples': sp_randint(20, 50), 
             'min_child_weight': [1e-5, 1e-3, 1e-2, 1e-1, 1, 1e1, 1e2, 1e3, 1e4],
             'subsample': sp_uniform(loc=0.2, scale=0.8), 
             'colsample_bytree': sp_uniform(loc=0.4, scale=0.6),
             'reg_alpha': [0, 1e-1, 1, 2, 5, 7, 10, 50, 100],
             'reg_lambda': [0, 1e-1, 1, 5, 10, 20, 50, 100]}

In [184]:
scorer = make_scorer(f1_score, average = 'weighted')

In [185]:
classifier = LGBMClassifier(random_state=300, silent=True, metric='None', n_jobs=4, n_estimators=10000)

find_parameters = RandomizedSearchCV(
    estimator=classifier, param_distributions=parameter_tuning, 
    n_iter=1000,
    scoring=scorer,
    cv=5,
    refit=True,
    random_state=300,
    verbose=False)

In [186]:
find_parameters.fit(X_train, y_train, **parameters)
print('Best score : {} with parameters: {} '.format(find_parameters.best_score_, find_parameters.best_params_))

Training until validation scores don't improve for 20 rounds
[100]	valid's multi_logloss: 1.07803
[200]	valid's multi_logloss: 1.03725
[300]	valid's multi_logloss: 1.03694
[400]	valid's multi_logloss: 1.03694
[500]	valid's multi_logloss: 1.03694
[600]	valid's multi_logloss: 1.03694
Early stopping, best iteration is:
[646]	valid's multi_logloss: 1.03694
Training until validation scores don't improve for 20 rounds
[100]	valid's multi_logloss: 1.03886
[200]	valid's multi_logloss: 1.03806
[300]	valid's multi_logloss: 1.03799
[400]	valid's multi_logloss: 1.03798
[500]	valid's multi_logloss: 1.03798
[600]	valid's multi_logloss: 1.03798
[700]	valid's multi_logloss: 1.03798
[800]	valid's multi_logloss: 1.03798
[900]	valid's multi_logloss: 1.03798
[1000]	valid's multi_logloss: 1.03798
[1100]	valid's multi_logloss: 1.03798
[1200]	valid's multi_logloss: 1.03798
Early stopping, best iteration is:
[1206]	valid's multi_logloss: 1.03798
Training until validation scores don't improve for 20 rounds
[10

/Users/sam/opt/anaconda3/lib/python3.6/site-packages/sklearn/model_selection/_validation.py:614: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/engine.py", line 228, in train
    booster = Booster(params=params, train_set=train_set)
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/basic.py", line 1714, in __init__
    train_set.construct().handle,
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/basic.py", line 1085, in construct
    categorical_feature=self.categorical_feature, params=self.params)
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/basic.py", line 887, in _lazy_init
    self.__init_from_np2d(data, params_str, ref_dataset)
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/basic.py", line 937, in __init_fro

Training until validation scores don't improve for 20 rounds
Early stopping, best iteration is:
[1]	valid's multi_logloss: 1.09819
Training until validation scores don't improve for 20 rounds
[100]	valid's multi_logloss: 1.07337
[200]	valid's multi_logloss: 1.07322
[300]	valid's multi_logloss: 1.07321
[400]	valid's multi_logloss: 1.07321
[500]	valid's multi_logloss: 1.07321
[600]	valid's multi_logloss: 1.07321
[700]	valid's multi_logloss: 1.07321
[800]	valid's multi_logloss: 1.07321
Early stopping, best iteration is:
[781]	valid's multi_logloss: 1.07321
Training until validation scores don't improve for 20 rounds
[100]	valid's multi_logloss: 1.07283
[200]	valid's multi_logloss: 1.07283
[300]	valid's multi_logloss: 1.07283
Early stopping, best iteration is:
[375]	valid's multi_logloss: 1.07283
Training until validation scores don't improve for 20 rounds
[100]	valid's multi_logloss: 1.07123
[200]	valid's multi_logloss: 1.07108
[300]	valid's multi_logloss: 1.07107
[400]	valid's multi_logl

/Users/sam/opt/anaconda3/lib/python3.6/site-packages/sklearn/model_selection/_validation.py:614: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/engine.py", line 228, in train
    booster = Booster(params=params, train_set=train_set)
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/basic.py", line 1714, in __init__
    train_set.construct().handle,
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/basic.py", line 1085, in construct
    categorical_feature=self.categorical_feature, params=self.params)
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/basic.py", line 887, in _lazy_init
    self.__init_from_np2d(data, params_str, ref_dataset)
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/basic.py", line 937, in __init_fro

[100]	valid's multi_logloss: 1.07597
[200]	valid's multi_logloss: 1.07571
[300]	valid's multi_logloss: 1.0757
[400]	valid's multi_logloss: 1.0757
[500]	valid's multi_logloss: 1.0757
Early stopping, best iteration is:
[488]	valid's multi_logloss: 1.0757
Training until validation scores don't improve for 20 rounds
[100]	valid's multi_logloss: 1.07615
[200]	valid's multi_logloss: 1.07595
[300]	valid's multi_logloss: 1.07594
[400]	valid's multi_logloss: 1.07594
[500]	valid's multi_logloss: 1.07594
[600]	valid's multi_logloss: 1.07594
Early stopping, best iteration is:
[644]	valid's multi_logloss: 1.07594
Training until validation scores don't improve for 20 rounds
[100]	valid's multi_logloss: 1.07698
[200]	valid's multi_logloss: 1.07666
[300]	valid's multi_logloss: 1.07665
[400]	valid's multi_logloss: 1.07665
Early stopping, best iteration is:
[432]	valid's multi_logloss: 1.07665
Training until validation scores don't improve for 20 rounds
[100]	valid's multi_logloss: 1.07662
[200]	valid's

...

/Users/sam/opt/anaconda3/lib/python3.6/site-packages/sklearn/model_selection/_validation.py:614: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/engine.py", line 228, in train
    booster = Booster(params=params, train_set=train_set)
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/basic.py", line 1714, in __init__
    train_set.construct().handle,
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/basic.py", line 1085, in construct
    categorical_feature=self.categorical_feature, params=self.params)
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/basic.py", line 887, in _lazy_init
    self.__init_from_np2d(data, params_str, ref_dataset)
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/basic.py", line 937, in __init_fro

[100]	valid's multi_logloss: 1.07364
[200]	valid's multi_logloss: 1.07346
[300]	valid's multi_logloss: 1.07345
[400]	valid's multi_logloss: 1.07345
[500]	valid's multi_logloss: 1.07345
[600]	valid's multi_logloss: 1.07345
[700]	valid's multi_logloss: 1.07345
[800]	valid's multi_logloss: 1.07345
[900]	valid's multi_logloss: 1.07345
[1000]	valid's multi_logloss: 1.07345
[1100]	valid's multi_logloss: 1.07345
Early stopping, best iteration is:
[1139]	valid's multi_logloss: 1.07345
Training until validation scores don't improve for 20 rounds
Early stopping, best iteration is:
[66]	valid's multi_logloss: 1.07303
Training until validation scores don't improve for 20 rounds
[100]	valid's multi_logloss: 1.07114
[200]	valid's multi_logloss: 1.07092
[300]	valid's multi_logloss: 1.07091
[400]	valid's multi_logloss: 1.07091
[500]	valid's multi_logloss: 1.07091
[600]	valid's multi_logloss: 1.07091
[700]	valid's multi_logloss: 1.07091
Early stopping, best iteration is:
[762]	valid's multi_logloss: 1.

/Users/sam/opt/anaconda3/lib/python3.6/site-packages/sklearn/model_selection/_validation.py:614: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/engine.py", line 228, in train
    booster = Booster(params=params, train_set=train_set)
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/basic.py", line 1714, in __init__
    train_set.construct().handle,
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/basic.py", line 1085, in construct
    categorical_feature=self.categorical_feature, params=self.params)
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/basic.py", line 887, in _lazy_init
    self.__init_from_np2d(data, params_str, ref_dataset)
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/basic.py", line 937, in __init_fro

[300]	valid's multi_logloss: 1.01772
Early stopping, best iteration is:
[330]	valid's multi_logloss: 1.01755
Training until validation scores don't improve for 20 rounds
[100]	valid's multi_logloss: 1.0219
[200]	valid's multi_logloss: 1.01901
[300]	valid's multi_logloss: 1.0185
Early stopping, best iteration is:
[356]	valid's multi_logloss: 1.01841
Training until validation scores don't improve for 20 rounds
[100]	valid's multi_logloss: 1.01997
[200]	valid's multi_logloss: 1.01642
[300]	valid's multi_logloss: 1.01545
[400]	valid's multi_logloss: 1.01514
Early stopping, best iteration is:
[450]	valid's multi_logloss: 1.01506
Training until validation scores don't improve for 20 rounds
[100]	valid's multi_logloss: 1.02153
[200]	valid's multi_logloss: 1.01771
[300]	valid's multi_logloss: 1.01652
[400]	valid's multi_logloss: 1.01597
[500]	valid's multi_logloss: 1.01568
[600]	valid's multi_logloss: 1.01552
[700]	valid's multi_logloss: 1.01543
[800]	valid's multi_logloss: 1.01538
[900]	valid

/Users/sam/opt/anaconda3/lib/python3.6/site-packages/sklearn/model_selection/_validation.py:614: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/engine.py", line 228, in train
    booster = Booster(params=params, train_set=train_set)
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/basic.py", line 1714, in __init__
    train_set.construct().handle,
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/basic.py", line 1085, in construct
    categorical_feature=self.categorical_feature, params=self.params)
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/basic.py", line 887, in _lazy_init
    self.__init_from_np2d(data, params_str, ref_dataset)
  File "/Users/sam/opt/anaconda3/lib/python3.6/site-packages/lightgbm/basic.py", line 937, in __init_fro

In [187]:
best_parameters = find_parameters.best_params_
best_parameters

{'colsample_bytree': 0.40337178522780726,
 'learning_rate ': 1,
 'max_depth': 2,
 'min_child_samples': 31,
 'min_child_weight': 100.0,
 'num_leaves': 4,
 'reg_alpha': 0,
 'reg_lambda': 5,
 'subsample': 0.5245927790861843}

In [188]:
best_parameters_model = lgb.LGBMClassifier(**best_parameters)
best_parameters_model.set_params(**best_parameters)

LGBMClassifier(colsample_bytree=0.40337178522780726, learning_rate =1,
               max_depth=2, min_child_samples=31, min_child_weight=100.0,
               num_leaves=4, reg_alpha=0, reg_lambda=5,
               subsample=0.5245927790861843)

In [189]:
clf = best_parameters_model.fit(X_train, y_train)

In [295]:
clf = GradientBoostingClassifier(learning_rate=1, max_depth=2, n_estimators=1000, random_state=0)

In [296]:
clf.fit(X_train, y_train)

GradientBoostingClassifier(learning_rate=1, max_depth=2, n_estimators=1000,
                           random_state=0)

In [297]:
y_preds = clf.predict(X_test)

In [298]:
np.mean(np.asarray(y_test) == y_preds)

0.42903575297941493

In [299]:
this_week = pd.read_csv("/Users/sam/Documents/projects/premier_league_predictions/current_gameweek.csv", index_col=0)

In [300]:
preds = []

this_week = this_week.drop(['away_ppg_home_team','home_ppg_away_team'], axis=1)

this_week = imp.transform(this_week)


for result in clf.predict(this_week):
    if result == 0:
        preds.append("home")
    elif result == 1:
        preds.append("away")
    else:
        preds.append("draw")
    
preds

['home',
 'home',
 'draw',
 'draw',
 'home',
 'draw',
 'draw',
 'home',
 'home',
 'home']

In [ ]:
print(classification_report(y_test, y_preds))

In [ ]:
def plot_learning_curve(estimator, title, X, y, axes=None, ylim=None, cv=None,
                        n_jobs=None, train_sizes=[0.1,0.2,0.3,0.4,0.5,0.6,0.7,0.8,0.9,1]):
    """
    Generate 3 plots: the test and training learning curve, the training
    samples vs fit times curve, the fit times vs score curve.

    Parameters
    ----------
    estimator : estimator instance
        An estimator instance implementing `fit` and `predict` methods which
        will be cloned for each validation.

    title : str
        Title for the chart.

    X : array-like of shape (n_samples, n_features)
        Training vector, where ``n_samples`` is the number of samples and
        ``n_features`` is the number of features.

    y : array-like of shape (n_samples) or (n_samples, n_features)
        Target relative to ``X`` for classification or regression;
        None for unsupervised learning.

    axes : array-like of shape (3,), default=None
        Axes to use for plotting the curves.

    ylim : tuple of shape (2,), default=None
        Defines minimum and maximum y-values plotted, e.g. (ymin, ymax).

    cv : int, cross-validation generator or an iterable, default=None
        Determines the cross-validation splitting strategy.
        Possible inputs for cv are:

          - None, to use the default 5-fold cross-validation,
          - integer, to specify the number of folds.
          - :term:`CV splitter`,
          - An iterable yielding (train, test) splits as arrays of indices.

        For integer/None inputs, if ``y`` is binary or multiclass,
        :class:`StratifiedKFold` used. If the estimator is not a classifier
        or if ``y`` is neither binary nor multiclass, :class:`KFold` is used.

        Refer :ref:`User Guide <cross_validation>` for the various
        cross-validators that can be used here.

    n_jobs : int or None, default=None
        Number of jobs to run in parallel.
        ``None`` means 1 unless in a :obj:`joblib.parallel_backend` context.
        ``-1`` means using all processors. See :term:`Glossary <n_jobs>`
        for more details.

    train_sizes : array-like of shape (n_ticks,)
        Relative or absolute numbers of training examples that will be used to
        generate the learning curve. If the ``dtype`` is float, it is regarded
        as a fraction of the maximum size of the training set (that is
        determined by the selected validation method), i.e. it has to be within
        (0, 1]. Otherwise it is interpreted as absolute sizes of the training
        sets. Note that for classification the number of samples usually have
        to be big enough to contain at least one sample from each class.
        (default: np.linspace(0.1, 1.0, 5))
    """
    if axes is None:
        _, axes = plt.subplots(1, 3, figsize=(20, 5))

    axes[0].set_title(title)
    if ylim is not None:
        axes[0].set_ylim(*ylim)
    axes[0].set_xlabel("Training examples")
    axes[0].set_ylabel("Score")

    train_sizes, train_scores, test_scores, fit_times, _ = \
        learning_curve(estimator, X, y, cv=cv, n_jobs=n_jobs,
                       train_sizes=train_sizes,
                       return_times=True)
    train_scores_mean = np.mean(train_scores, axis=1)
    train_scores_std = np.std(train_scores, axis=1)
    test_scores_mean = np.mean(test_scores, axis=1)
    test_scores_std = np.std(test_scores, axis=1)
    fit_times_mean = np.mean(fit_times, axis=1)
    fit_times_std = np.std(fit_times, axis=1)

    # Plot learning curve
    axes[0].grid()
    axes[0].fill_between(train_sizes, train_scores_mean - train_scores_std,
                         train_scores_mean + train_scores_std, alpha=0.1,
                         color="r")
    axes[0].fill_between(train_sizes, test_scores_mean - test_scores_std,
                         test_scores_mean + test_scores_std, alpha=0.1,
                         color="g")
    axes[0].plot(train_sizes, train_scores_mean, 'o-', color="r",
                 label="Training score")
    axes[0].plot(train_sizes, test_scores_mean, 'o-', color="g",
                 label="Cross-validation score")
    axes[0].legend(loc="best")

    # Plot n_samples vs fit_times
    axes[1].grid()
    axes[1].plot(train_sizes, fit_times_mean, 'o-')
    axes[1].fill_between(train_sizes, fit_times_mean - fit_times_std,
                         fit_times_mean + fit_times_std, alpha=0.1)
    axes[1].set_xlabel("Training examples")
    axes[1].set_ylabel("fit_times")
    axes[1].set_title("Scalability of the model")

    # Plot fit_time vs score
    axes[2].grid()
    axes[2].plot(fit_times_mean, test_scores_mean, 'o-')
    axes[2].fill_between(fit_times_mean, test_scores_mean - test_scores_std,
                         test_scores_mean + test_scores_std, alpha=0.1)
    axes[2].set_xlabel("fit_times")
    axes[2].set_ylabel("Score")
    axes[2].set_title("Performance of the model")

    return plt


fig, axes = plt.subplots(3, 2, figsize=(10, 15))

title = "Learning Curves (LGM)"
# Cross validation with 100 iterations to get smoother mean test and train
# score curves, each time with 20% data randomly selected as a validation set.
cv = ShuffleSplit(n_splits=100, test_size=0.2, random_state=0)

plot_learning_curve(clf, title, X_train, y_train, axes=axes[:, 0], ylim=(0.01, 1.01),
                    cv=cv, n_jobs=4)

plt.show()